### Create window aggregate features 

Next feature type we will consider is window aggregate feature. 
These are features generated by aggregating data within specific time frame.  


In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:42:36 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:42:36 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:42:36 | INFO     | SDK version: 0.6.0.dev121
16:42:36 | INFO     | No catalog activated.
16:42:36 | INFO     | 11 feature lists, 66 features deployed
16:42:36 | INFO     | Using profile: tutorial
16:42:36 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:42:36 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:42:37 | INFO     | SDK version: 0.6.0.dev121
16:42:37 | INFO     | No catalog activated.
16:42:38 | INFO     | 11 feature lists, 66 features deployed
16:42:38 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYINVOICE event table.
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")

#### Do window aggregation from GROCERYINVOICE


In [3]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid).
groceryinvoice_view_by_customer = groceryinvoice_view.groupby(['GroceryCustomerGuid'])

In [4]:
# Get Latest invoice Amount for the customer
customer_latest_invoice_amount = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="latest",
    feature_names=["CUSTOMER_Latest_invoice_Amount"],
    windows=[None]
)["CUSTOMER_Latest_invoice_Amount"]

In [5]:
# Set desired windows
windows = ['14d', '28d']

In [6]:
# Get Count of invoices for the customer
customer_count_of_invoice_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    method="count",
    feature_names=[
        "CUSTOMER_Count_of_invoice"
        + "_" + w for w in windows
    ],
    windows=windows
)

In [7]:
# Get Avg of Amount for the customer over time.
customer_avg_of_invoice_amount_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="avg",
    feature_names=[
        "CUSTOMER_Avg_of_invoice_Amount"
        + "_" + w for w in windows
    ],
    windows=windows
)

In [8]:
# Get Std of Amount for the customer over time.
customer_std_of_invoice_amount_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="std",
    feature_names=[
        "CUSTOMER_Std_of_invoice_Amount"
        + "_" + w for w in windows
    ],
    windows=windows
)

#### Preview a feature group

In [9]:
feature_group = fb.FeatureGroup([
    customer_latest_invoice_amount,
    customer_count_of_invoice_14d_28d,
    customer_avg_of_invoice_amount_14d_28d,
    customer_std_of_invoice_amount_14d_28d,
])

In [10]:
# Check the primary entity of the feature group
feature_group.primary_entity

 {
   'name': 'customer',
   'created_at': '2023-11-27T15:39:09.477000',
   'updated_at': '2023-11-27T15:39:19.968000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [11]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [12]:
# Preview feature_group
feature_group.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2   
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9   
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47   
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd   
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0   
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db   
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c   
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597   
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301   

   CUSTOMER_Latest_invoice_Amount  CUSTOMER_Count_of_invoice_14d  \
0                            6.72                              0   
1                           12.28                              0   
2                           10.02                              0   
3                           53.09                              5   
4                           21.74                              3   
5                           15.30                              1   
6                           14.55                              2   
7                            0.89                             12   
8                           11.43                              4   
9                            2.00                              6   

   CUSTOMER_Count_of_invoice_28d  CUSTOMER_Avg_of_invoice_Amount_14d  \
0                              1                                 NaN   
1                              0                                 NaN   
2                              4                                 NaN   
3                             10                           15.626000   
4                              6                           15.560000   
5                              1                           15.300000   
6                              4                           14.560000   
7                             29                            3.209167   
8                              4                           11.317500   
9                              8                            4.568333   

   CUSTOMER_Avg_of_invoice_Amount_28d  CUSTOMER_Std_of_invoice_Amount_14d  \
0                            6.720000                                 NaN   
1                                 NaN                                 NaN   
2                           26.415000                                 NaN   
3                           26.450000                           19.000809   
4                           10.555000                            6.681337   
5                           15.300000                            0.000000   
6                           15.050000                            0.010000   
7                            5.220345                            4.154236   
8                           11.317500                            4.526297   
9                           10.431250                            2.832763   

   CUSTOMER_Std_of_invoice_Amount_28d  
0                            0.000000  
1                                 NaN  
2                           19.563101  
3                           26.837185  
4                            7.307384  
5                            0.000000  
6                           10.109369  
7                            8.163223  
8                            4.526297  
9                           11.335775

#### Save features into catalog 
With feature groups we can do it in one call.

In [13]:
feature_group.save()

Done! |████████████████████████████████████████| 100% in 13.0s (0.08%/s)        
Loading Feature(s) |████████████████████████████████████████| 7/7 [100%] in 0.6s


#### Add description and see feature definition files

In [14]:
# Add description
customer_latest_invoice_amount.update_description("Latest invoice Amount for the customer")
# See feature definition file
customer_latest_invoice_amount.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("6564b7ebbeba6c193e0fe3bc"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="latest",\n    windows=[None],\n    feature_names=["CUSTOMER_Latest_invoice_Amount"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["CUSTOMER_Latest_invoice_Amount"]\noutput = feat\noutput.save(_id=ObjectId("6564b8f0a69f1a9a43bdfd7d"))\n'

In [15]:
# Add description
customer_count_of_invoice_14d = customer_count_of_invoice_14d_28d["CUSTOMER_Count_of_invoice_14d"]
customer_count_of_invoice_14d.update_description(
    "Sum of invoice Amount for the customer over a 14d period."
)
customer_count_of_invoice_28d = customer_count_of_invoice_14d_28d["CUSTOMER_Count_of_invoice_28d"]
customer_count_of_invoice_28d.update_description(
    "Count of invoice for the customer over a 28d period."
)
# See feature definition file
customer_count_of_invoice_28d.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("6564b7ebbeba6c193e0fe3bc"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column=None,\n    method="count",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Count_of_invoice_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["CUSTOMER_Count_of_invoice_28d"]\nfeat_1 = feat.copy()\nfeat_1[feat.isnull()] = 0\nfeat_1.name = "CUSTOMER_Count_of_invoice_28d"\noutput = feat_1\noutput.save(_id=ObjectId("6564b8f0a69f1a9a43bdfd80"))\n'

In [16]:
# Add description
customer_avg_of_invoice_amount_14d = customer_avg_of_invoice_amount_14d_28d["CUSTOMER_Avg_of_invoice_Amount_14d"]
customer_avg_of_invoice_amount_14d.update_description(
    "Avg of invoice Amount for the customer over a 14d period."
)
customer_avg_of_invoice_amount_28d = customer_avg_of_invoice_amount_14d_28d["CUSTOMER_Avg_of_invoice_Amount_28d"]
customer_avg_of_invoice_amount_28d.update_description(
    "Avg of invoice Amount for the customer over a 28d period."
)
# See feature definition file
customer_avg_of_invoice_amount_28d.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("6564b7ebbeba6c193e0fe3bc"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="avg",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Avg_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["CUSTOMER_Avg_of_invoice_Amount_28d"]\noutput = feat\noutput.save(_id=ObjectId("6564b8f0a69f1a9a43bdfd83"))\n'

In [17]:
# Add description
customer_std_of_invoice_amount_14d = customer_std_of_invoice_amount_14d_28d["CUSTOMER_Std_of_invoice_Amount_14d"]
customer_std_of_invoice_amount_14d.update_description(
    "Std of invoice Amount for the customer over a 14d period."
)
customer_std_of_invoice_amount_28d = customer_std_of_invoice_amount_14d_28d["CUSTOMER_Std_of_invoice_Amount_28d"]
customer_std_of_invoice_amount_28d.update_description(
    "Std of invoice Amount for the customer over a 28d period."
)

# See feature definition file
customer_std_of_invoice_amount_28d.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("6564b7ebbeba6c193e0fe3bc"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="std",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Std_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["CUSTOMER_Std_of_invoice_Amount_28d"]\noutput = feat\noutput.save(_id=ObjectId("6564b8f0a69f1a9a43bdfd85"))\n'

### Concepts in this tutorial
- [Aggregate Features](https://docs.featurebyte.com/latest/about/glossary/#aggregate-features)
- [Window Aggregate Features](https://docs.featurebyte.com/latest/about/glossary/#aggregates-over-a-window)

#### SDK reference for
- [View.groupby()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/#see-also)
- [Groupby.aggregate_over()](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)
- [List of aggregate functions](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)
- [FeatureGroup](https://docs.featurebyte.com/latest/reference/core/feature_group/)
- [FeatureGroup.save()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature_group.FeatureGroup.save/)